## Simple Strategy Backtesting

In [1]:
from account_system import *
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
pio.renderers.default = "notebook"

In [2]:
BCH_BTC = pd.read_csv('../data/bch-btc_OHLC.csv')
BCH_USD = pd.read_csv('../data/bch-usd_OHLC.csv')
BTC_USD = pd.read_csv('../data/btc-usd_OHLC.csv')

In [3]:
naive_position_sizer_constructor = NaivePositionSizer
naive_execution_handler_constructor = ExecutionHandler
position_size = 5

In [4]:
def naive_market_impact_calculator(df_price_with_signal, impact_pct):
    price_actual = df_price_with_signal['price'].copy()
    buy_index = df_price_with_signal['signal'].apply(lambda x: x.value) == Signal.BUY.value
    sell_index = df_price_with_signal['signal'].apply(lambda x: x.value) == Signal.SELL.value
    price_actual[buy_index] *= (1 + impact_pct)
    price_actual[sell_index] *= (1 - impact_pct)
    return price_actual

__A naive position sizer__ buys `position_suggested` amount of `target_asset` upon every `BUY` signal, and dumps all existing positions in `target_asset` upon a `SELL` signal.<span style="color:red"> To make the matter simple, we assume the `BUY` and `SELL` are executed through __market orders__ </span>(which should never be done in real life), <span style="color:red">and that they are executed right before the next tick arrives (which never happens in real life).</span>

__A naive execution handler__ fills in the detail of the execution of these market orders. For each tick where trade happens, it specifies `asset_bought`, `asset_sold`, `price_actual`, `amount_bought`, `amount_sold` and `commission`. The transaction cost is reflected in `price_actual`, `amount_bought/sold` and `commission`. 

- As all trades are executed using market order, the position of the `target_asset` is always assumed to fill. For example, when the signal is `BUY`, we issue a market order to sell the `target_asset`. The `asset_sold` there would be `target_asset`, and the `amount_sold` is the proposed `position_suggested`. 
- `price_actual` is the interpolated price at which the trade actaully takes place. Just like the latest `price`, it's stated in terms of (units of `base_asset`/`target_asset`). It takes market impact into account. 
- The `asset_bought` is the `base_asset`, and the `amount_bought` is calculated using `amount_sold` * `price_actual`. 
- The commission is quoted in `target_asset` always. This isn't how the fee is actually charged. We do it here for implementational convinience. 

__Market impact__ <span style="color:red"> is naively modeled as a percentage of the last-traded price (with buy, it's always slightly higher; with sell, it's always slightly slower)</span>. In reality it should always be modelled based on order-book data.

## 0. Monkey's Choice

A naive signal generator does nothing more than generating a `BUY`, `SELL` and `HOLD` at random.

In [5]:
signal_generator_constructor = NaiveSignalGenerator

### 0.0 A quick demo for results

In [91]:
np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = BTC_USD.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.000
commission_rate=0.025

In [92]:
%%time
### Signal Generation
naive_signal_generator = signal_generator_constructor(df_price)
df_price_with_signal = naive_signal_generator.get_price_with_signal()


### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()


### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)


### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_monkeys_choice = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)

Wall time: 20.2 s


In [93]:
%%time
################## TIME WARNING: 25s #######################
BTC_USD_monkey_account = Account(BTC_USD_monkeys_choice.tail(5000), initial_equity=100000, inital_equity_exists_as='USD')
BTC_USD_monkey_account.process_transaction_history()
BTC_USD_monkey_result = BTC_USD_monkey_account.show_assets_with_transactions(target_asset='BTC', base_asset='USD')

Wall time: 13.9 s


__Transaction Details__

In [95]:
BTC_USD_monkey_account.transaction_history.tail(10)

time     price       signal  position_suggested  \
57427 2020-11-20 23:51:00  18644.87  Signal.SELL                   0   
57428 2020-11-20 23:52:00  18650.29  Signal.HOLD                   0   
57429 2020-11-20 23:53:00  18657.25   Signal.BUY                   5   
57430 2020-11-20 23:54:00  18656.03   Signal.BUY                   5   
57431 2020-11-20 23:55:00  18651.11   Signal.BUY                   5   
57432 2020-11-20 23:56:00  18652.71  Signal.SELL                  15   
57433 2020-11-20 23:57:00  18645.43  Signal.SELL                   0   
57434 2020-11-20 23:58:00  18689.97  Signal.SELL                   0   
57435 2020-11-20 23:59:00  18675.25  Signal.SELL                   0   
57436 2020-11-21 00:00:00  18702.87  Signal.SELL                   0   

      asset_bought asset_sold  price_actual  amount_bought  amount_sold  \
57427          USD        BTC      18644.87           0.00         0.00   
57428          BTC        USD      18650.29           0.00         0.00   
57429          BTC        USD      18657.25           5.00     93286.25   
57430          BTC        USD      18656.03           5.00     93280.15   
57431          BTC        USD      18651.11           5.00     93255.55   
57432          USD        BTC      18652.71      279790.65        15.00   
57433          USD        BTC      18645.43           0.00         0.00   
57434          USD        BTC      18689.97           0.00         0.00   
57435          USD        BTC      18675.25           0.00         0.00   
57436          USD        BTC      18702.87           0.00         0.00   

       commission  
57427       0.000  
57428       0.000  
57429       0.125  
57430       0.125  
57431       0.125  
57432       0.375  
57433       0.000  
57434       0.000  
57435       0.000  
57436       0.000

__Account Situation Details__

In [94]:
BTC_USD_monkey_result.tail(10)

time        USD   BTC     price       signal  \
4990 2020-11-20 23:51:00  369510.25 -15.0  18644.87  Signal.SELL   
4991 2020-11-20 23:52:00  369510.25 -15.0  18650.29  Signal.HOLD   
4992 2020-11-20 23:53:00  276224.00 -10.0  18657.25   Signal.BUY   
4993 2020-11-20 23:54:00  182943.85  -5.0  18656.03   Signal.BUY   
4994 2020-11-20 23:55:00   89688.30   0.0  18651.11   Signal.BUY   
4995 2020-11-20 23:56:00  369478.95 -15.0  18652.71  Signal.SELL   
4996 2020-11-20 23:57:00  369478.95 -15.0  18645.43  Signal.SELL   
4997 2020-11-20 23:58:00  369478.95 -15.0  18689.97  Signal.SELL   
4998 2020-11-20 23:59:00  369478.95 -15.0  18675.25  Signal.SELL   
4999 2020-11-21 00:00:00  369478.95 -15.0  18702.87  Signal.SELL   

      position_suggested  position_in_base  
4990                   0         89404.075  
4991                   0         89322.775  
4992                   5         89218.250  
4993                   5         89230.325  
4994                   5         89254.800  
4995                  15         89254.425  
4996                   0         89363.625  
4997                   0         88695.525  
4998                   0         88916.325  
4999                   0         88502.025

In [88]:
BTC_USD_monkey_account.assets.head(5)

time           USD   BTC
52437 2020-11-17 12:41:00  9.148568e+05   5.0
52438 2020-11-17 12:42:00  9.148568e+05   5.0
52439 2020-11-17 12:43:00  9.148568e+05   5.0
52440 2020-11-17 12:44:00  1.256430e+06 -15.0
52441 2020-11-17 12:45:00  1.171067e+06 -10.0

### 0.1 How market impact kills a monkey

With BTC-USD pair, for a monkey that starts with 1,000,000 capital, if he trades for 5000 minutes (a little less than 3.5 days):
    
- He loses around 1.2% with or without the 2.5% commission fee.
- He loses around <span style="color:red"> 2.8% with a 0.005% market impact </span>.


In [12]:
%%time
############### TIME WARNING: 50s ###############
np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = BTC_USD.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.000
commission_rate=0.00

### Signal Generation
naive_signal_generator = signal_generator_constructor(df_price)
df_price_with_signal = naive_signal_generator.get_price_with_signal()


### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)


### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()


### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_monkeys_choice = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)

BTC_USD_monkey_account = Account(BTC_USD_monkeys_choice.tail(5000), initial_equity=1000000, inital_equity_exists_as='USD')
BTC_USD_monkey_account.process_transaction_history()
BTC_USD_monkey_no_transaction_cost = BTC_USD_monkey_account.show_assets_with_transactions(target_asset='BTC', base_asset='USD')

Wall time: 31.6 s


In [13]:
BTC_USD_monkey_no_transaction_cost.tail(10)

time         USD   BTC     price       signal  \
4990 2020-11-20 23:51:00  1269510.25 -15.0  18644.87  Signal.SELL   
4991 2020-11-20 23:52:00  1269510.25 -15.0  18650.29  Signal.HOLD   
4992 2020-11-20 23:53:00  1176224.00 -10.0  18657.25   Signal.BUY   
4993 2020-11-20 23:54:00  1082943.85  -5.0  18656.03   Signal.BUY   
4994 2020-11-20 23:55:00   989688.30   0.0  18651.11   Signal.BUY   
4995 2020-11-20 23:56:00  1269478.95 -15.0  18652.71  Signal.SELL   
4996 2020-11-20 23:57:00  1269478.95 -15.0  18645.43  Signal.SELL   
4997 2020-11-20 23:58:00  1269478.95 -15.0  18689.97  Signal.SELL   
4998 2020-11-20 23:59:00  1269478.95 -15.0  18675.25  Signal.SELL   
4999 2020-11-21 00:00:00  1269478.95 -15.0  18702.87  Signal.SELL   

      position_suggested  position_in_base  
4990                   0          989837.2  
4991                   0          989755.9  
4992                   5          989651.5  
4993                   5          989663.7  
4994                   5          989688.3  
4995                  15          989688.3  
4996                   0          989797.5  
4997                   0          989129.4  
4998                   0          989350.2  
4999                   0          988935.9

In [14]:
%%time
############### TIME WARNING: 50s ###############
np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = BTC_USD.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.000
commission_rate=0.025

### Signal Generation
naive_signal_generator = signal_generator_constructor(df_price)
df_price_with_signal = naive_signal_generator.get_price_with_signal()
### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()
### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_monkeys_choice = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)

BTC_USD_monkey_account = Account(BTC_USD_monkeys_choice.tail(5000), initial_equity=1000000, inital_equity_exists_as='USD')
BTC_USD_monkey_account.process_transaction_history()
BTC_USD_monkey_with_commission = BTC_USD_monkey_account.show_assets_with_transactions(target_asset='BTC', base_asset='USD')

Wall time: 36.9 s


In [15]:
BTC_USD_monkey_with_commission.tail(10)

time         USD   BTC     price       signal  \
4990 2020-11-20 23:51:00  1269510.25 -15.0  18644.87  Signal.SELL   
4991 2020-11-20 23:52:00  1269510.25 -15.0  18650.29  Signal.HOLD   
4992 2020-11-20 23:53:00  1176224.00 -10.0  18657.25   Signal.BUY   
4993 2020-11-20 23:54:00  1082943.85  -5.0  18656.03   Signal.BUY   
4994 2020-11-20 23:55:00   989688.30   0.0  18651.11   Signal.BUY   
4995 2020-11-20 23:56:00  1269478.95 -15.0  18652.71  Signal.SELL   
4996 2020-11-20 23:57:00  1269478.95 -15.0  18645.43  Signal.SELL   
4997 2020-11-20 23:58:00  1269478.95 -15.0  18689.97  Signal.SELL   
4998 2020-11-20 23:59:00  1269478.95 -15.0  18675.25  Signal.SELL   
4999 2020-11-21 00:00:00  1269478.95 -15.0  18702.87  Signal.SELL   

      position_suggested  position_in_base  
4990                   0        989404.075  
4991                   0        989322.775  
4992                   5        989218.250  
4993                   5        989230.325  
4994                   5        989254.800  
4995                  15        989254.425  
4996                   0        989363.625  
4997                   0        988695.525  
4998                   0        988916.325  
4999                   0        988502.025

In [16]:
%%time
############### TIME WARNING: 50s ###############
np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = BTC_USD.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025

### Signal Generation
naive_signal_generator = signal_generator_constructor(df_price)
df_price_with_signal = naive_signal_generator.get_price_with_signal()


### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)


### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()

### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_monkeys_choice = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)

BTC_USD_monkey_account = Account(BTC_USD_monkeys_choice.tail(5000), initial_equity=1000000, inital_equity_exists_as='USD')
BTC_USD_monkey_account.process_transaction_history()
BTC_USD_monkey_with_market_impact_and_commission = BTC_USD_monkey_account.show_assets_with_transactions(target_asset='BTC', base_asset='USD')

Wall time: 31.8 s


In [17]:
BTC_USD_monkey_with_market_impact_and_commission.tail(10)

time           USD   BTC     price       signal  \
4990 2020-11-20 23:51:00  1.253956e+06 -15.0  18644.87  Signal.SELL   
4991 2020-11-20 23:52:00  1.253956e+06 -15.0  18650.29  Signal.HOLD   
4992 2020-11-20 23:53:00  1.160665e+06 -10.0  18657.25   Signal.BUY   
4993 2020-11-20 23:54:00  1.067380e+06  -5.0  18656.03   Signal.BUY   
4994 2020-11-20 23:55:00  9.741198e+05   0.0  18651.11   Signal.BUY   
4995 2020-11-20 23:56:00  1.253896e+06 -15.0  18652.71  Signal.SELL   
4996 2020-11-20 23:57:00  1.253896e+06 -15.0  18645.43  Signal.SELL   
4997 2020-11-20 23:58:00  1.253896e+06 -15.0  18689.97  Signal.SELL   
4998 2020-11-20 23:59:00  1.253896e+06 -15.0  18675.25  Signal.SELL   
4999 2020-11-21 00:00:00  1.253896e+06 -15.0  18702.87  Signal.SELL   

      position_suggested  position_in_base  
4990                   0     973849.556607  
4991                   0     973768.256607  
4992                   5     973659.067295  
4993                   5     973666.478287  
4994                   5     973686.290510  
4995                  15     973671.925977  
4996                   0     973781.125977  
4997                   0     973113.025977  
4998                   0     973333.825977  
4999                   0     972919.525977

In [18]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = BTC_USD_monkey_no_transaction_cost['time']
    ,y = BTC_USD_monkey_no_transaction_cost['position_in_base']
    , name='no transaction cost'
    ,mode='lines'
))
fig.add_trace(go.Scatter(
    x = BTC_USD_monkey_with_commission['time']
    ,y = BTC_USD_monkey_with_commission['position_in_base']
    , name='with {} commission'.format(commission_rate)
    ,mode='lines'
))
fig.add_trace(go.Scatter(
    x = BTC_USD_monkey_with_market_impact_and_commission['time']
    ,y = BTC_USD_monkey_with_market_impact_and_commission['position_in_base']
    , name='with {} commission, {}% market impact'.format(commission_rate, market_impact_pct*100)
    ,mode='lines'
))
fig.update_layout(title = 'How a monkey is ruined by market impact: an example on BTC-USD pairs'
                 ,hovermode = 'x unified')

### 1. A simple 75 - 25 quantile strategy

The idea is simple: sell when the price goes above the 75th historical quantile, and buy when the price falls below 25th historical quantile.

We use the last 5000 minutes as the trading period, and those prior data points as 75-25 quantile identifiers.

- The strategy fails on BTCUSD and BCHBTC because BTC is just too hot. For BTCUSD, not a single BUY signal was generated. For BCHBTC, Our strategy predicts that BTC price will fall once it hits its relative historical high, but it just doesn't. Another thing that might weakens our strategy is that we only SELL the `target_asset` to close a positive position. We will fix this in the next iteration of position sizer.

- The strategy works well on BCHUSD pair, harnessing that price increase in BCH during midnight Nov.20, at around 1:30 am. The price shot up from 246 to 257 in less than one hour, and stayed mostly above 255 till the end of the trading period. We captured that spike in price with the large position we built when BCH was around 245. However, the position was built in a pretty scary manner. <span style="color:red"> We kept upping our bets when the price stayed at 245, which is no different than putting more chips on the table with new information not providing any insights. __This flaw is inherent in the simplicity of the strategy__.</span> 

In [19]:
class ThresholdingSignalGenerator(SignalGenerator):
    def __init__(self, df_price, sell_threshold, buy_threshold):
        self.df_price = df_price
        self.sell_threshold = sell_threshold
        self.buy_threshold = buy_threshold
    
    def get_price_with_signal(self):
        self.df_price['signal'] = Signal.HOLD
        self.df_price['signal'][self.df_price['price'] > self.sell_threshold] = Signal.SELL
        self.df_price['signal'][self.df_price['price'] < self.buy_threshold] = Signal.BUY
        return self.df_price
    

In [20]:
%%time
############### TIME WARNING: 20.2s ###############
df = BTC_USD
trading_length = 5000
df_trading = BTC_USD.tail(trading_length)
df_param_identifying = BTC_USD.head(df.shape[0] - trading_length)
sell_quantile = 0.75
buy_quantile = 0.25
sell_threshold = df_param_identifying['close'].quantile(sell_quantile)
buy_threshold = df_param_identifying['close'].quantile(buy_quantile)


np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = df_trading.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025

### Signal Generation
thresholding_signal_generator = ThresholdingSignalGenerator(df_trading, sell_threshold, buy_threshold)
df_price_with_signal = thresholding_signal_generator.get_price_with_signal()



### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()
### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_thresholding_transaction_history = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)
BTC_USD_thresholding_account = Account(BTC_USD_thresholding_transaction_history, initial_equity=1000000, inital_equity_exists_as='USD')
BTC_USD_thresholding_account.process_transaction_history()
BTC_USD_thresholding = BTC_USD_thresholding_account.show_assets_with_transactions(target_asset=target_asset, base_asset=base_asset)

Wall time: 21.3 s


In [21]:
BTC_USD_thresholding

time        USD  BTC         price       signal  \
0    2020-11-17 12:41:00  1000000.0    0  17027.818337  Signal.SELL   
1    2020-11-17 12:42:00  1000000.0    0  17031.213022  Signal.SELL   
2    2020-11-17 12:43:00  1000000.0    0  17042.760537  Signal.SELL   
3    2020-11-17 12:44:00  1000000.0    0  17074.198543  Signal.SELL   
4    2020-11-17 12:45:00  1000000.0    0  17072.587214  Signal.SELL   
...                  ...        ...  ...           ...          ...   
4995 2020-11-20 23:56:00  1000000.0    0  18652.767264  Signal.SELL   
4996 2020-11-20 23:57:00  1000000.0    0  18648.608531  Signal.SELL   
4997 2020-11-20 23:58:00  1000000.0    0  18667.264284  Signal.SELL   
4998 2020-11-20 23:59:00  1000000.0    0  18689.099749  Signal.SELL   
4999 2020-11-21 00:00:00  1000000.0    0  18700.272767  Signal.SELL   

      position_suggested  position_in_base  
0                      0         1000000.0  
1                      0         1000000.0  
2                      0         1000000.0  
3                      0         1000000.0  
4                      0         1000000.0  
...                  ...               ...  
4995                   0         1000000.0  
4996                   0         1000000.0  
4997                   0         1000000.0  
4998                   0         1000000.0  
4999                   0         1000000.0  

[5000 rows x 7 columns]

In [22]:
fig = make_subplots(specs=[[{'secondary_y' : True}]])
fig.add_trace(go.Scatter(
    x = BTC_USD_thresholding['time']
    ,y = BTC_USD_thresholding['position_in_base']
    ,name = 'total position in {}'.format(base_asset)
    ,text = BTC_USD_thresholding['signal'].apply(lambda x: x.value)
))
fig.add_trace(go.Scatter(
    x = BTC_USD_thresholding['time']
    ,y = BTC_USD_thresholding['price']
    ,name = '{} price in {}'.format(target_asset, base_asset)
    ,opacity = 0.75
),secondary_y = True)
fig.update_layout(title='Quantile thresholding fails on {} {} pair'.format(target_asset, base_asset)
                 , hovermode = 'x unified')

In [23]:
%%time
############### TIME WARNING: 20.2s ###############
df = BCH_BTC
trading_length = 5000
df_trading = df.tail(trading_length)
df_param_identifying = BCH_BTC.head(df.shape[0] - trading_length)
sell_quantile = 0.75
buy_quantile = 0.25
sell_threshold = df_param_identifying['close'].quantile(sell_quantile)
buy_threshold = df_param_identifying['close'].quantile(buy_quantile)


np.random.seed(100)
target_asset = 'BCH'
base_asset = 'BTC'
df_price = df_trading.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025

### Signal Generation
thresholding_signal_generator = ThresholdingSignalGenerator(df_trading, sell_threshold, buy_threshold)
df_price_with_signal = thresholding_signal_generator.get_price_with_signal()



### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()
### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BCH_BTC_thresholding_transaction_history = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)
BCH_BTC_thresholding_account = Account(BCH_BTC_thresholding_transaction_history, initial_equity=13, inital_equity_exists_as=base_asset)
BCH_BTC_thresholding_account.process_transaction_history()
BCH_BTC_thresholding = BCH_BTC_thresholding_account.show_assets_with_transactions(target_asset=target_asset, base_asset=base_asset)

Wall time: 18.4 s


In [24]:
BCH_BTC_thresholding

time         BTC      BCH     price      signal  \
0    2020-11-15 19:03:00   12.922747      5.0  0.015450  Signal.BUY   
1    2020-11-15 19:04:00   12.845593     10.0  0.015430  Signal.BUY   
2    2020-11-15 19:05:00   12.768339     15.0  0.015450  Signal.BUY   
3    2020-11-15 19:06:00   12.691153     20.0  0.015436  Signal.BUY   
4    2020-11-15 19:08:00   12.614217     25.0  0.015387  Signal.BUY   
...                  ...         ...      ...       ...         ...   
4995 2020-11-20 23:54:00 -346.443701  24980.0  0.013900  Signal.BUY   
4996 2020-11-20 23:56:00 -346.513304  24985.0  0.013920  Signal.BUY   
4997 2020-11-20 23:57:00 -346.583024  24990.0  0.013943  Signal.BUY   
4998 2020-11-20 23:58:00 -346.652767  24995.0  0.013948  Signal.BUY   
4999 2020-11-20 23:59:00 -346.722471  25000.0  0.013940  Signal.BUY   

      position_suggested  position_in_base  
0                      5         12.874996  
1                      5         12.749893  
2                      5         12.625089  
3                      5         12.499882  
4                      5         12.373881  
...                  ...               ...  
4995                   5       -623.721701  
4996                   5       -623.347104  
4997                   5       -622.889153  
4998                   5       -622.900114  
4999                   5       -623.222471  

[5000 rows x 7 columns]

In [25]:
fig = make_subplots(specs=[[{'secondary_y' : True}]])
fig.add_trace(go.Scatter(
    x = BCH_BTC_thresholding['time']
    ,y = BCH_BTC_thresholding['position_in_base']
    ,name = 'total position in {}'.format(base_asset)
    ,text = BCH_BTC_thresholding['signal'].apply(lambda x: x.value)
))
fig.add_trace(go.Scatter(
    x = BCH_BTC_thresholding['time']
    ,y = BCH_BTC_thresholding['price']
    ,name = '{} price in {}'.format(target_asset, base_asset)
    ,opacity = 0.75
),secondary_y = True)
fig.update_layout(title='Quantile thresholding fails on {} {} pair'.format(target_asset, base_asset)
                 , hovermode = 'x unified')

In [26]:
%%time
############### TIME WARNING: 20.2s ###############
df = BCH_USD
trading_length = 5000
df_trading = df.tail(trading_length)
df_param_identifying = BCH_USD.head(df.shape[0] - trading_length)
sell_quantile = 0.75
buy_quantile = 0.25
sell_threshold = df_param_identifying['close'].quantile(sell_quantile)
buy_threshold = df_param_identifying['close'].quantile(buy_quantile)


np.random.seed(100)
target_asset = 'BCH'
base_asset = 'USD'
df_price = df_trading.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025

### Signal Generation
thresholding_signal_generator = ThresholdingSignalGenerator(df_trading, sell_threshold, buy_threshold)
df_price_with_signal = thresholding_signal_generator.get_price_with_signal()



### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()
### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BCH_USD_thresholding_transaction_history = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)
BCH_USD_thresholding_account = Account(BCH_USD_thresholding_transaction_history, initial_equity=1000000, inital_equity_exists_as=base_asset)
BCH_USD_thresholding_account.process_transaction_history()
BCH_USD_thresholding = BCH_USD_thresholding_account.show_assets_with_transactions(target_asset=target_asset, base_asset=base_asset)

Wall time: 10.7 s


In [27]:
BCH_USD_thresholding.tail(10)

time           USD      BCH       price       signal  \
4990 2020-11-20 23:51:00 -2.158523e+06  12770.0  259.221829  Signal.HOLD   
4991 2020-11-20 23:52:00 -2.158523e+06  12770.0  259.598690  Signal.HOLD   
4992 2020-11-20 23:53:00 -2.158523e+06  12770.0  259.500437  Signal.HOLD   
4993 2020-11-20 23:54:00 -2.158523e+06  12770.0  259.939677  Signal.HOLD   
4994 2020-11-20 23:55:00 -2.158523e+06  12770.0  260.002041  Signal.HOLD   
4995 2020-11-20 23:56:00 -2.158523e+06  12770.0  259.862096  Signal.HOLD   
4996 2020-11-20 23:57:00 -2.158523e+06  12770.0  260.130803  Signal.HOLD   
4997 2020-11-20 23:58:00 -2.158523e+06  12770.0  260.386899  Signal.HOLD   
4998 2020-11-20 23:59:00 -2.158523e+06  12770.0  260.196905  Signal.HOLD   
4999 2020-11-21 00:00:00 -2.158523e+06  12770.0  260.328080  Signal.HOLD   

      position_suggested  position_in_base  
4990                   0      1.151421e+06  
4991                   0      1.156233e+06  
4992                   0      1.154978e+06  
4993                   0      1.160587e+06  
4994                   0      1.161384e+06  
4995                   0      1.159597e+06  
4996                   0      1.163028e+06  
4997                   0      1.166298e+06  
4998                   0      1.163872e+06  
4999                   0      1.165547e+06

In [28]:
fig = make_subplots(specs=[[{'secondary_y' : True}]])
fig.add_trace(go.Scatter(
    x = BCH_USD_thresholding['time']
    ,y = BCH_USD_thresholding['position_in_base']
    ,name = 'total position in {}'.format(base_asset)
    ,text = BCH_USD_thresholding['signal'].apply(lambda x: x.value)
))
fig.add_trace(go.Scatter(
    x = BCH_USD_thresholding['time']
    ,y = BCH_USD_thresholding['price']
    ,name = '{} price in {}'.format(target_asset, base_asset)
    ,opacity = 0.75
),secondary_y = True)
fig.update_layout(title='Quantile thresholding works well on BCH USD pair'
                 , hovermode = 'x unified')

## 2. An MA strategy

MA strategy seems not able to catpure BTC's momentum well. It still needs further exploration.

In [42]:
class MA_SignalGenerator(SignalGenerator):
    def __init__(self, df_price, MA_window_small, MA_window_large):
        self.df_price = df_price
        self.MA_window_small = MA_window_small
        self.MA_window_large = MA_window_large
        
    def get_price_with_signal(self):
        MA_window_small = self.MA_window_small
        MA_window_large = self.MA_window_large
        self.df_price['MA{}'.format(MA_window_small)] = self.df_price['price'].rolling(MA_window_small).mean()
        self.df_price['MA{}'.format(MA_window_large)] = self.df_price['price'].rolling(MA_window_large).mean()
        self.df_price['signal'] = Signal.HOLD
        small_exceeds_large = np.logical_and(
        (self.df_price['MA{}'.format(MA_window_small)] < self.df_price['MA{}'.format(MA_window_large)]).shift(1)
            , self.df_price['MA{}'.format(MA_window_small)] > self.df_price['MA{}'.format(MA_window_large)]
        )
        small_trails_large = np.logical_and(
        (self.df_price['MA{}'.format(MA_window_small)] > self.df_price['MA{}'.format(MA_window_large)]).shift(1)
            , self.df_price['MA{}'.format(MA_window_small)] < self.df_price['MA{}'.format(MA_window_large)]
        )
        self.df_price['signal'][small_exceeds_large] = Signal.BUY
        self.df_price['signal'][small_trails_large] = Signal.SELL
        return self.df_price

In [51]:
%%time
df = BTC_USD
trading_length = 6000
df_trading = df.tail(trading_length)

np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = df_trading.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025


### Signal Generation
MA_window_small = 5
MA_window_large = 60
MA_signal_generator = MA_SignalGenerator(df_price, MA_window_small, MA_window_large)
df_price_with_signal = MA_signal_generator.get_price_with_signal()

Wall time: 12 ms


In [70]:
BTC_USD_MA_transaction_history

time     price        MA5          MA60       signal  \
52437 2020-11-17 12:41:00  17027.78  17024.420  16992.928000  Signal.HOLD   
52438 2020-11-17 12:42:00  17041.77  17031.624  16994.460500  Signal.HOLD   
52439 2020-11-17 12:43:00  17054.45  17038.984  16996.314333  Signal.HOLD   
52440 2020-11-17 12:44:00  17079.50  17046.554  16998.407333  Signal.HOLD   
52441 2020-11-17 12:45:00  17071.78  17055.056  17000.341500  Signal.HOLD   
...                   ...       ...        ...           ...          ...   
57432 2020-11-20 23:56:00  18652.71  18653.478  18654.746167  Signal.HOLD   
57433 2020-11-20 23:57:00  18645.43  18652.506  18655.272167  Signal.HOLD   
57434 2020-11-20 23:58:00  18689.97  18659.050  18656.124333   Signal.BUY   
57435 2020-11-20 23:59:00  18675.25  18662.894  18656.706000  Signal.HOLD   
57436 2020-11-21 00:00:00  18702.87  18673.246  18657.902667  Signal.HOLD   

       position_suggested asset_bought asset_sold  price_actual  \
52437                   0          BTC        USD  17027.780000   
52438                   0          BTC        USD  17041.770000   
52439                   0          BTC        USD  17054.450000   
52440                   0          BTC        USD  17079.500000   
52441                   0          BTC        USD  17071.780000   
...                   ...          ...        ...           ...   
57432                   0          BTC        USD  18652.710000   
57433                   0          BTC        USD  18645.430000   
57434                   5          BTC        USD  18690.904499   
57435                   0          BTC        USD  18675.250000   
57436                   0          BTC        USD  18702.870000   

       amount_bought   amount_sold  commission  
52437            0.0      0.000000       0.000  
52438            0.0      0.000000       0.000  
52439            0.0      0.000000       0.000  
52440            0.0      0.000000       0.000  
52441            0.0      0.000000       0.000  
...              ...           ...         ...  
57432            0.0      0.000000       0.000  
57433            0.0      0.000000       0.000  
57434            5.0  93454.522493       0.125  
57435            0.0      0.000000       0.000  
57436            0.0      0.000000       0.000  

[5000 rows x 12 columns]

In [55]:
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()

In [60]:
%%time
naive_execution_handler = naive_execution_handler_constructor(df_position
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_MA_transaction_history = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)


Wall time: 36 ms


In [62]:
BTC_USD_MA_account = Account(BTC_USD_MA_transaction_history, initial_equity=1000000, inital_equity_exists_as='USD')

In [65]:
BTC_USD_MA_account.process_transaction_history()

In [66]:
BTC_USD_MA_account.assets

time           USD  BTC
51437 2020-11-16 20:01:00  1.000000e+06  0.0
51438 2020-11-16 20:02:00  1.000000e+06  0.0
51439 2020-11-16 20:03:00  1.000000e+06  0.0
51440 2020-11-16 20:04:00  1.000000e+06  0.0
51441 2020-11-16 20:05:00  1.000000e+06  0.0
...                   ...           ...  ...
57432 2020-11-20 23:56:00  1.004204e+06  0.0
57433 2020-11-20 23:57:00  1.004204e+06  0.0
57434 2020-11-20 23:58:00  9.107498e+05  5.0
57435 2020-11-20 23:59:00  9.107498e+05  5.0
57436 2020-11-21 00:00:00  9.107498e+05  5.0

[6000 rows x 3 columns]

In [77]:
%%time
df = BTC_USD
trading_length = 6000
df_trading = df.tail(trading_length)

np.random.seed(100)
target_asset = 'BTC'
base_asset = 'USD'
df_price = df_trading.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025


### Signal Generation
MA_window_small = 5
MA_window_large = 60
MA_signal_generator = MA_SignalGenerator(df_price, MA_window_small, MA_window_large)
df_price_with_signal = MA_signal_generator.get_price_with_signal().copy()



### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()
### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position.tail(5000)
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BTC_USD_MA_transaction_history = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)
BTC_USD_MA_account = Account(BTC_USD_MA_transaction_history, initial_equity=1000000, inital_equity_exists_as='USD')
BTC_USD_MA_account.process_transaction_history()
BTC_USD_MA = BTC_USD_MA_account.show_assets_with_transactions(target_asset=target_asset, base_asset=base_asset)

Wall time: 1.52 s


In [78]:
fig = make_subplots(specs=[[{'secondary_y' : True}]])
fig.add_trace(go.Scatter(
    x = BTC_USD_MA['time']
    ,y = BTC_USD_MA['position_in_base']
    ,name = 'total position in {}'.format(base_asset)
    ,text = BTC_USD_MA['signal'].apply(lambda x: x.value)
))
fig.add_trace(go.Scatter(
    x = BTC_USD_MA['time']
    ,y = BTC_USD_MA['price']
    ,name = '{} price in {}'.format(target_asset, base_asset)
    ,opacity = 0.75
),secondary_y = True)
fig.update_layout(title='MA{} crossing MA{} fails on {} {} pair'.format(MA_window_small, MA_window_large, target_asset, base_asset)
                 , hovermode = 'x unified')

In [79]:
%%time
df = BCH_USD
trading_length = 6000
df_trading = df.tail(trading_length)

np.random.seed(100)
target_asset = 'BCH'
base_asset = 'USD'
df_price = df_trading.pipe(extract_price_data, price_name='close')
market_impact_pct = 0.00005
commission_rate=0.025


### Signal Generation
MA_window_small = 5
MA_window_large = 60
MA_signal_generator = MA_SignalGenerator(df_price, MA_window_small, MA_window_large)
df_price_with_signal = MA_signal_generator.get_price_with_signal()



### Price with market impact
price_actual_naive = naive_market_impact_calculator(df_price_with_signal, market_impact_pct)
### Position_suggested_generation
naive_position_sizer = naive_position_sizer_constructor(df_price_with_signal, position_size=5)
df_position = naive_position_sizer.get_price_signal_position()
### Execution Handling
naive_execution_handler = naive_execution_handler_constructor(df_position.tail(5000)
                                                             ,target_asset=target_asset
                                                             ,base_asset=base_asset)
BCH_USD_MA_transaction_history = naive_execution_handler.get_execution_details(price_actual=price_actual_naive, commission_rate=commission_rate)
BCH_USD_MA_account = Account(BCH_USD_MA_transaction_history, initial_equity=1000000, inital_equity_exists_as='USD')
BCH_USD_MA_account.process_transaction_history()
BCH_USD_MA = BCH_USD_MA_account.show_assets_with_transactions(target_asset=target_asset, base_asset=base_asset)

Wall time: 1.37 s


In [80]:
BCH_USD_MA

time             USD  BCH   price       signal  \
0    2020-11-17 09:03:00  1000000.000000  0.0  251.59  Signal.HOLD   
1    2020-11-17 09:05:00  1000000.000000  0.0  251.80  Signal.HOLD   
2    2020-11-17 09:06:00  1000000.000000  0.0  251.71  Signal.HOLD   
3    2020-11-17 09:07:00   998740.737040  5.0  251.84   Signal.BUY   
4    2020-11-17 09:08:00   998740.737040  5.0  251.84  Signal.HOLD   
...                  ...             ...  ...     ...          ...   
4995 2020-11-20 23:56:00   998697.616197  5.0  259.81  Signal.HOLD   
4996 2020-11-20 23:57:00   998697.616197  5.0  260.20  Signal.HOLD   
4997 2020-11-20 23:58:00   998697.616197  5.0  260.48  Signal.HOLD   
4998 2020-11-20 23:59:00   998697.616197  5.0  260.32  Signal.HOLD   
4999 2020-11-21 00:00:00   998697.616197  5.0  260.29  Signal.HOLD   

      position_suggested  position_in_base  
0                      0    1000000.000000  
1                      0    1000000.000000  
2                      0    1000000.000000  
3                      5     999999.812040  
4                      0     999999.812040  
...                  ...               ...  
4995                   0     999977.541197  
4996                   0     999979.491197  
4997                   0     999980.891197  
4998                   0     999980.091197  
4999                   0     999979.941197  

[5000 rows x 7 columns]

In [82]:
fig = make_subplots(specs=[[{'secondary_y' : True}]])
fig.add_trace(go.Scatter(
    x = BCH_USD_MA['time']
    ,y = BCH_USD_MA['position_in_base']
    ,name = 'total position in {}'.format(base_asset)
    ,text = BCH_USD_MA['signal'].apply(lambda x: x.value)
))
fig.add_trace(go.Scatter(
    x = BCH_USD_MA['time']
    ,y = BCH_USD_MA['price']
    ,name = '{} price in {}'.format(target_asset, base_asset)
    ,opacity = 0.75
),secondary_y = True)
fig.update_layout(title='MA{} crossing MA{} fails on BCH USD pair'.format(MA_window_small, MA_window_large)
                 , hovermode = 'x unified')